In [1]:
import copy
import datetime as dt
import importlib
import matplotlib.pyplot as plt
import os
import numpy as np
import pandas as pd
import pathlib
import sys
import time
import pickle
from typing import Union
import warnings
from datetime import datetime
from pyswarm import pso  # Install with: pip install pyswarm
warnings.filterwarnings("ignore")
from info_grupos import empirical_vars_to_avoid, frac_vars_special_cases_list
from utilities.utils import HelperFunctions, SSPModelForCalibration, SectoralDiffReport, NonEnergySectoralDiffReport, ErrorFunctions
import logging
from sisepuede.manager.sisepuede_examples import SISEPUEDEExamples

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# Record the start time
start_time = time.time()

# Initialize helper functions
helper_functions = HelperFunctions()

In [4]:
# Paths
SRC_FILE_PATH = os.getcwd()
build_path = lambda PATH: os.path.abspath(os.path.join(*PATH))
DATA_PATH = build_path([SRC_FILE_PATH, "..", "data"])
OUTPUT_PATH = build_path([SRC_FILE_PATH, "..", "output"])
REAL_DATA_FILE_PATH = build_path([DATA_PATH, "real_data.csv"])
MISC_FILES_PATH = build_path([SRC_FILE_PATH, 'misc'])
OPT_CONFIG_FILES_PATH = build_path([SRC_FILE_PATH, 'config'])
OPT_OUTPUT_PATH = build_path([SRC_FILE_PATH,"..", "output"])

In [5]:
OPT_CONFIG_FILES_PATH

'/home/tony-ubuntu/decision_sciences/ssp_data_calibration/src/config'

In [6]:
# Make sure the output directory exists
os.makedirs(OPT_OUTPUT_PATH, exist_ok=True)

In [7]:
# Get important params from the YAML file

try:
    yaml_file = 'croatia_opt_config.yaml' #TODO: CHANGE IT TO sys.argv[1]
except IndexError:
    raise ValueError("YAML configuration file must be provided as a command-line argument.")

param_dict = helper_functions.get_parameters_from_yaml(build_path([OPT_CONFIG_FILES_PATH, yaml_file]))

target_region = param_dict['target_region']
iso_alpha_3 = param_dict['iso_alpha_3']
detailed_diff_report_flag = param_dict['detailed_diff_report_flag']
error_type = param_dict['error_type'] 
unique_id = datetime.now().strftime("%Y%m%d%H%M%S")

logging.info(f"Starting optimization for {target_region} (ISO code: {iso_alpha_3}). Detailed diff report: {'enabled' if detailed_diff_report_flag else 'disabled'}, Error type: {error_type}.")

2025-01-31 16:49:31,836 - INFO - Starting optimization for croatia (ISO code: HRV). Detailed diff report: enabled, Error type: rmse.


In [8]:
# Load input dataset
examples = SISEPUEDEExamples()
cr = examples("input_data_frame")
df_input = pd.read_csv(REAL_DATA_FILE_PATH)

# Add missing columns and reformat the input datas
df_input = df_input.rename(columns={'period': 'time_period'})
df_input = helper_functions.add_missing_cols(cr, df_input.copy())
df_input = df_input.drop(columns='iso_code3')

In [9]:
# Load frac_vars mapping excel
frac_vars_mapping = pd.read_excel(build_path([MISC_FILES_PATH, 'frac_vars_mapping.xlsx']), sheet_name='frac_vars')
frac_vars_mapping

frac_var_name  \
0      frac_agrc_agriculture_production_lost   
1    frac_agrc_bevs_and_spices_cl1_temperate   
2     frac_agrc_bevs_and_spices_cl1_tropical   
3          frac_agrc_bevs_and_spices_cl2_dry   
4          frac_agrc_bevs_and_spices_cl2_wet   
..                                       ...   
817                 frac_waso_recycled_paper   
818               frac_waso_recycled_plastic   
819        frac_waso_recycled_rubber_leather   
820              frac_waso_recycled_textiles   
821                  frac_waso_recycled_wood   

                 frac_var_name_prefix  special_case  
0    frac_agrc_agriculture_production             1  
1       frac_agrc_bevs_and_spices_cl1             0  
2       frac_agrc_bevs_and_spices_cl1             0  
3       frac_agrc_bevs_and_spices_cl2             0  
4       frac_agrc_bevs_and_spices_cl2             0  
..                                ...           ...  
817                frac_waso_recycled             0  
818                frac_waso_recycled             0  
819                frac_waso_recycled             0  
820                frac_waso_recycled             0  
821                frac_waso_recycled             0  

[822 rows x 3 columns]

In [10]:
# Load the stressed variables mapping file
stressed_vars_mapping = pd.read_excel(build_path([MISC_FILES_PATH, 'stressed_variables_report.xlsx']))
stressed_vars_mapping

variable_name      Subsector  \
0                                  area_gnrl_country_ha  SocioEconomic   
1       avgload_trns_freight_tonne_per_vehicle_aviation         Energy   
2     avgload_trns_freight_tonne_per_vehicle_rail_fr...         Energy   
3     avgload_trns_freight_tonne_per_vehicle_road_he...         Energy   
4     avgload_trns_freight_tonne_per_vehicle_water_b...         Energy   
...                                                 ...            ...   
2211                            yf_agrc_pulses_tonne_ha          AFOLU   
2212                              yf_agrc_rice_tonne_ha          AFOLU   
2213                        yf_agrc_sugar_cane_tonne_ha          AFOLU   
2214                            yf_agrc_tubers_tonne_ha          AFOLU   
2215              yf_agrc_vegetables_and_vines_tonne_ha          AFOLU   

      is_stressed  l_bound  u_bound  group_id  max_value  needs check  
0               0      1.0      1.0       NaN        NaN          NaN  
1               1      0.5      1.5       0.0        NaN          NaN  
2               1      0.5      1.5       0.0        NaN          NaN  
3               1      0.5      1.5       0.0        NaN          NaN  
4               1      0.5      1.5       0.0        NaN          NaN  
...           ...      ...      ...       ...        ...          ...  
2211            1      0.5      1.5       NaN        NaN          NaN  
2212            1      0.5      1.5       NaN        NaN          NaN  
2213            1      0.5      1.5       NaN        NaN          NaN  
2214            1      0.5      1.5       NaN        NaN          NaN  
2215            1      0.5      1.5       NaN        NaN          NaN  

[2216 rows x 8 columns]

In [11]:
# Subset the stressed variables mapping file to is_stressed = 1
stressed_vars_mapping = stressed_vars_mapping[stressed_vars_mapping['is_stressed'] == 1]

# Drop NaN values from the stressed variables mapping file
stressed_vars_mapping = stressed_vars_mapping.dropna(subset=['group_id'])

# Reset the index of the stressed variables mapping file
stressed_vars_mapping = stressed_vars_mapping.reset_index(drop=True)

# Set group_id as integer
stressed_vars_mapping['group_id'] = stressed_vars_mapping['group_id'].astype(int)

# Set group_id as string
# stressed_vars_mapping['group_id'] = stressed_vars_mapping['group_id'].astype(str)

In [12]:
stressed_vars_mapping.group_id.unique()

array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16,
       19, 17, 18, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33,
       34, 35, 36, 37, 38, 40, 41, 39, 42, 43, 44, 45, 46, 47, 48, 49, 50,
       51, 52, 53])

In [13]:
# Get the frac_vars that are going to be stressed
frac_vars_to_stress = [var for var in stressed_vars_mapping['variable_name'].values if var.startswith('frac_')]
frac_vars_to_stress

['frac_trns_mtkm_dem_freight_aviation',
 'frac_trns_mtkm_dem_freight_rail_freight',
 'frac_trns_mtkm_dem_freight_road_heavy_freight',
 'frac_trns_mtkm_dem_freight_water_borne']

In [15]:
# Subset frac_vars_mapping to only include the frac_vars that are going to be stressed
frac_vars_mapping = frac_vars_mapping[frac_vars_mapping['frac_var_name'].isin(frac_vars_to_stress)].reset_index(drop=True)
frac_vars_mapping

frac_var_name        frac_var_name_prefix  \
0            frac_trns_mtkm_dem_freight_aviation  frac_trns_mtkm_dem_freight   
1        frac_trns_mtkm_dem_freight_rail_freight  frac_trns_mtkm_dem_freight   
2  frac_trns_mtkm_dem_freight_road_heavy_freight  frac_trns_mtkm_dem_freight   
3         frac_trns_mtkm_dem_freight_water_borne  frac_trns_mtkm_dem_freight   

   special_case  
0             0  
1             0  
2             0  
3             0

In [16]:
# Get group ids of the vars that are stressed
group_ids = stressed_vars_mapping[stressed_vars_mapping["is_stressed"] == 1]["group_id"].unique()
n_groups = len(group_ids)
print(group_ids)
print(n_groups)
print(type(group_ids[0]))



[ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 19 17 18 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 40 41 39 42 43 44 45 46 47
 48 49 50 51 52 53]
54
<class 'numpy.int64'>


In [17]:
# Get the lower and upper bounds for each group
l_bounds = stressed_vars_mapping.groupby("group_id")["l_bound"].first().values
u_bounds = stressed_vars_mapping.groupby("group_id")["u_bound"].first().values

print(f"{10*'#'}bounds{10*'#'}")
print(l_bounds)
print(u_bounds)

print(f"{10*'#'}bounds vector size{10*'#'}")
print(len(l_bounds))
print(len(u_bounds))

##########bounds##########
[0.5 0.6 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5
 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5 0.5
 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.8 0.5 0.5]
[1.5 1.6 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5
 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5 1.5
 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.8 1.5 1.5]
##########bounds vector size##########
54
54


In [18]:
# Create a dictionary with the group ids as keys and the corresponding variable names as values
group_vars_dict = {}
for group_id in group_ids:
    group_vars_dict[group_id] = stressed_vars_mapping[stressed_vars_mapping["group_id"] == group_id]["variable_name"].values

group_vars_dict

{0: array(['avgload_trns_freight_tonne_per_vehicle_aviation',
        'avgload_trns_freight_tonne_per_vehicle_rail_freight',
        'avgload_trns_freight_tonne_per_vehicle_road_heavy_freight',
        'avgload_trns_freight_tonne_per_vehicle_water_borne'], dtype=object),
 1: array(['ef_agrc_biomass_fruits_tonne_co2_ha',
        'ef_agrc_biomass_nuts_tonne_co2_ha',
        'ef_agrc_biomass_other_woody_perennial_tonne_co2_ha'], dtype=object),
 2: array(['ef_enfu_combustion_tonne_co2_per_tj_fuel_ammonia',
        'ef_enfu_stationary_combustion_tonne_ch4_per_tj_fuel_ammonia',
        'ef_enfu_stationary_combustion_tonne_n2o_per_tj_fuel_ammonia',
        'ef_trns_mobile_combustion_water_borne_kg_n2o_per_tj_ammonia'],
       dtype=object),
 3: array(['ef_enfu_combustion_tonne_co2_per_tj_fuel_biofuels',
        'ef_enfu_stationary_combustion_tonne_ch4_per_tj_fuel_biofuels',
        'ef_enfu_stationary_combustion_tonne_n2o_per_tj_fuel_biofuels',
        'ef_trns_mobile_combustion_public_kg_ch4

In [19]:
logging.info("Initializing SSP model...")
ssp_model = SSPModelForCalibration(energy_model_flag=False)
diff_report_helpers = NonEnergySectoralDiffReport(MISC_FILES_PATH, iso_alpha_3, init_year=2015)
ef = ErrorFunctions()

2025-01-31 15:55:42,105 - INFO - Initializing SSP model...
2025-01-31 15:55:43,202 - INFO - Successfully initialized SISEPUEDEFileStructure.
2025-01-31 15:55:43,202 - INFO - Successfully initialized SISEPUEDEFileStructure.
2025-01-31 15:55:43,208 - WARNING - Missing key dict_dimensional_keys: key time_series not found. Tables that rely on the time_series will not have index checking.
2025-01-31 15:55:43,208 - WARNING - Missing key dict_dimensional_keys: key time_series not found. Tables that rely on the time_series will not have index checking.
2025-01-31 15:55:43,210 - INFO - 	Setting export engine to 'csv'.
2025-01-31 15:55:43,210 - INFO - 	Setting export engine to 'csv'.
2025-01-31 15:55:43,215 - WARNING - No index fields defined. Index field values will not be checked when writing to tables.
2025-01-31 15:55:43,215 - WARNING - No index fields defined. Index field values will not be checked when writing to tables.
2025-01-31 15:55:43,216 - INFO - Successfully instantiated table ANAL

In [20]:
# Simulation model
def simulation_model(df: pd.DataFrame) -> pd.DataFrame:
    """
    Function that simulates outputs based on the scaled inputs.
    """
    sim_output_df = ssp_model.run_ssp_simulation(df)
    
    # Handle empty DataFrame
    if sim_output_df is None or sim_output_df.empty:
        logging.warning("Simulation Output DataFrame is empty. Returning an empty DataFrame.")
        return pd.DataFrame()

    return sim_output_df


In [23]:
# Define the objective function
def objective_function(x):
    # x: scaling factors for each group_id
    # print("Scaling Factors Candidate Solution: \n", x)
    # print("Candidate Solution Size: \n", x.shape)
    modified_df = df_input.copy()
    
    # TODO: Vectorize this loop
    for group_id in group_vars_dict:
        # print(group_id)
        for var in group_vars_dict[group_id]:
            # print(var)
            # print(modified_df[var])
            # print('index: ', group_id)
            # print(x[group_id])
            modified_df[var] = modified_df[var] * x[group_id]
    
    # TODO: Handle frac var normalization
    norm_df = helper_functions.simple_frac_normalization(modified_df, frac_vars_mapping)
    
    # TODO: Run the model
    sim_output_df = simulation_model(norm_df)
    # TODO: Calculate the error
    exit()

In [24]:
# Initialize the PSO optimizer
best_solution, best_value = pso(objective_function, l_bounds, u_bounds)

Scaling Factors Candidate Solution: 
 [0.64040125 1.42040431 1.35625892 0.96883567 1.04086933 0.97585618
 1.28065182 1.6548372  1.33645612 0.72849024 0.74697005 0.78637003
 0.87954949 1.48574647 1.40673748 1.10672426 1.4473771  0.88762275
 0.91565698 0.72684323 1.26606709 1.09603459 0.68772369 1.15285944
 1.49243184 1.27947572 1.0045167  0.73699462 0.56654636 1.24809336
 0.9826823  1.02045159 1.2585713  0.53898281 1.22329162 1.22884753
 1.66846536 1.71054913 1.54170978 1.41381299 1.13105352 1.04543911
 1.01097883 0.90042563 0.80529458 0.85090241 1.77313739 0.80364921
 1.66516169 1.679562   1.71179567 1.76188262 1.40786989]
Candidate Solution Size: 
 (53,)
0
avgload_trns_freight_tonne_per_vehicle_aviation
0     70
1     70
2     70
3     70
4     70
5     70
6     70
7     70
8     70
9     70
10    70
11    70
12    70
13    70
14    70
15    70
16    70
17    70
18    70
19    70
20    70
21    70
22    70
23    70
24    70
25    70
26    70
27    70
28    70
29    70
30    70
31    7

2025-01-31 15:58:41,821 - INFO - Running AFOLU model
2025-01-31 15:58:41,821 - INFO - Running AFOLU model
2025-01-31 15:58:42,042 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:42,042 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:42,044 - INFO - Running CircularEconomy model
2025-01-31 15:58:42,044 - INFO - Running CircularEconomy model
2025-01-31 15:58:42,111 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:42,111 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:42,113 - INFO - Running IPPU model
2025-01-31 15:58:42,113 - INFO - Running IPPU model
2025-01-31 15:58:42,205 - INFO - IPPU model run successfully completed
2025-01-31 15:58:42,205 - INFO - IPPU model run successfully complete

Scaling Factors Candidate Solution: 
 [0.82843154 1.08318765 1.22117034 1.29500125 1.73373281 1.4840704
 0.81464131 1.30084106 1.59206292 1.06198714 0.74333268 1.11338314
 0.95746621 0.84473878 0.72053695 1.10466557 0.7455382  0.62837197
 0.78231908 0.82187826 1.02755616 0.98059568 0.89383747 0.63160711
 1.49088534 0.58525165 1.30188222 1.21623167 1.24411869 1.40138777
 0.97384657 0.76578735 0.96894801 1.26428446 0.81058963 0.58091388
 1.57266788 1.73148985 1.27151303 1.31009924 0.82258199 1.14134159
 0.83274059 1.62623647 1.2100498  1.31520587 0.87601101 1.37801223
 1.07047099 1.00733173 1.40795137 1.7211326  0.81971859]
Candidate Solution Size: 
 (53,)
0
avgload_trns_freight_tonne_per_vehicle_aviation
0     70
1     70
2     70
3     70
4     70
5     70
6     70
7     70
8     70
9     70
10    70
11    70
12    70
13    70
14    70
15    70
16    70
17    70
18    70
19    70
20    70
21    70
22    70
23    70
24    70
25    70
26    70
27    70
28    70
29    70
30    70
31    70

2025-01-31 15:58:42,869 - INFO - Running AFOLU model
2025-01-31 15:58:42,869 - INFO - Running AFOLU model
2025-01-31 15:58:43,058 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:43,058 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:43,060 - INFO - Running CircularEconomy model
2025-01-31 15:58:43,060 - INFO - Running CircularEconomy model
2025-01-31 15:58:43,125 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:43,125 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:43,126 - INFO - Running IPPU model
2025-01-31 15:58:43,126 - INFO - Running IPPU model
2025-01-31 15:58:43,222 - INFO - IPPU model run successfully completed
2025-01-31 15:58:43,222 - INFO - IPPU model run successfully complete

Scaling Factors Candidate Solution: 
 [0.94325728 1.13723988 1.25187929 1.29297054 0.9575067  1.397239
 1.72281508 1.01453917 1.40974206 1.39809865 0.82593442 1.30602214
 0.77328601 1.20690736 1.12761871 1.39616576 0.83387708 0.91973566
 0.86997103 1.3169447  1.05319872 1.02995544 1.335401   0.74153438
 1.38520117 0.76548246 1.28848531 0.80282004 1.23293529 0.53847886
 1.34384656 1.13426113 0.92071475 1.32705073 0.54875323 1.23466059
 1.52342255 1.03760209 0.93775944 0.87066378 0.81985592 1.33099461
 1.27172759 1.15083462 0.8170385  1.33130064 1.79767571 0.9843088
 1.77835781 1.60869629 0.86410206 1.35087866 0.57814086]
Candidate Solution Size: 
 (53,)
0
avgload_trns_freight_tonne_per_vehicle_aviation
0     70
1     70
2     70
3     70
4     70
5     70
6     70
7     70
8     70
9     70
10    70
11    70
12    70
13    70
14    70
15    70
16    70
17    70
18    70
19    70
20    70
21    70
22    70
23    70
24    70
25    70
26    70
27    70
28    70
29    70
30    70
31    70
3

...

2025-01-31 15:58:56,780 - INFO - Running AFOLU model
2025-01-31 15:58:56,780 - INFO - Running AFOLU model
2025-01-31 15:58:57,013 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:57,013 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:57,015 - INFO - Running CircularEconomy model
2025-01-31 15:58:57,015 - INFO - Running CircularEconomy model
2025-01-31 15:58:57,093 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:57,093 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:57,095 - INFO - Running IPPU model
2025-01-31 15:58:57,095 - INFO - Running IPPU model
2025-01-31 15:58:57,200 - INFO - IPPU model run successfully completed
2025-01-31 15:58:57,200 - INFO - IPPU model run successfully complete

Scaling Factors Candidate Solution: 
 [1.20223191 0.68999181 1.49193224 1.36745951 1.15532249 0.8606962
 1.65225474 1.36603158 1.43542961 0.57262604 1.32113751 1.28461297
 0.77593866 0.68496376 0.83745145 0.90714723 1.31632166 0.98112376
 0.89207936 0.63959376 1.18213235 0.74447522 1.28049094 1.14106164
 0.51544899 1.149742   1.1212187  1.17330706 0.50025697 0.58012698
 1.30935294 0.58876715 0.66967773 0.5158818  1.33872119 0.83441015
 0.9014724  1.7204435  1.03823516 0.98782804 0.9022701  1.62489019
 1.42276796 1.48851727 1.6184182  1.26561473 1.15171268 1.39804876
 1.40402723 1.14799983 1.17473961 1.43358717 0.63418882]
Candidate Solution Size: 
 (53,)
0
avgload_trns_freight_tonne_per_vehicle_aviation
0     70
1     70
2     70
3     70
4     70
5     70
6     70
7     70
8     70
9     70
10    70
11    70
12    70
13    70
14    70
15    70
16    70
17    70
18    70
19    70
20    70
21    70
22    70
23    70
24    70
25    70
26    70
27    70
28    70
29    70
30    70
31    70

2025-01-31 15:58:57,963 - INFO - Running AFOLU model
2025-01-31 15:58:57,963 - INFO - Running AFOLU model
2025-01-31 15:58:58,239 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:58,239 - INFO - AFOLU model run successfully completed
2025-01-31 15:58:58,241 - INFO - Running CircularEconomy model
2025-01-31 15:58:58,241 - INFO - Running CircularEconomy model
2025-01-31 15:58:58,664 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:58,664 - ERROR - Error running CircularEconomy model: Invalid summations found: some categories exceed the sum threshold.See the calculation of dict_waso_comp_biogas_check.
2025-01-31 15:58:58,665 - INFO - Running IPPU model
2025-01-31 15:58:58,665 - INFO - Running IPPU model
2025-01-31 15:58:58,775 - INFO - IPPU model run successfully completed
2025-01-31 15:58:58,775 - INFO - IPPU model run successfully complete

KeyboardInterrupt: 

: 